In [1]:
def f3d(figure, **kwargs):
    return make_frame3d(figure, **kwargs)


#@options(grid=(8,8,8), colors=['white', 'gray'], alpha=.4, resize_factor=1.2, show_axes=False, show_labels=True, label_names=['x','y','z'], show_ticks=True)
def make_frame3d(figure, grid=(8,8,8), colors=['white', 'gray'], alpha=.3, resize_factor=1.2, show_axes=False, show_labels=True, label_names=['x','y','z'], show_ticks=True, **kwargs):
    """
    Generate a complete frame for a 3D graphics object.
    This is a workaround for the lack of complete frames in 
    Sage 3D plots. It creates a background frame behind the
    plot, set ticks, gridlines and labels as text3d objects
    at locations determined from the bounding box of the 
    graphic object ``figure``.

    INPUT:

    - ``figure`` -- a 3D graphic object, as an instance of
        :class:`~sage.plot.plot3d.base.Graphics3d`
    - ``grid`` -- list with the number of gridlines and ticks
        in the x, y and z direction respectively
    - ``colors`` -- list with the background frame color and
        gridline color respectively
    - ``alpha`` -- transparency of the background frame
    - ``resize_factor`` -- string for the z-axis label
    - ``cube_ratio`` -- string for the z-axis label
    - ``show_labels`` -- Boolean. Show or not the labels
    - ``label_names`` -- ist of strings with the x-axis label,
        the y-axis label and the z-axis label.
    - ``show_ticks`` -- Boolean. Show or not the tickmarks
    - ``**kwds`` -- options (e.g. aspect_ratio) for the
        3D output object

    OUTPUT:

    - the 3D graphic object with text3d labels added.

    EXAMPLE::

         sage: pd=plot3d(sin(x^2 + y^2),(x,-5,5),(y,-5,5),
       plot_points=200,opacity=0.5)

cr=circle((0,0),1.22,color="red")
show(pd+cr)
    """
    fig_boundings = tuple(zip(*figure.bounding_box()))
    lower_left = [ur - (ur - ll)*resize_factor for ll, ur in fig_boundings]
    upper_right = [ll + (ur - ll)*resize_factor for ll, ur in fig_boundings]
    frame_color, gridline_color = colors
    figure += set_frame3d(lower_left, upper_right, grid, frame_color, gridline_color, show_axes, show_labels, label_names, show_ticks, alpha=alpha, **kwargs)
    if 'aspect_ratio' not in kwargs.keys():
        dx, dy, dz = (ur - ll for ll, ur in fig_boundings)
        dmax = max(dx,dy,dz)
        ratio = [dmax/k for k in (dx,dy,dz)]
        figure.aspect_ratio(ratio)
    return figure


def set_frame3d(lower_left, upper_right, grid, frame_color, gridline_color, show_axes=True, show_labels=True, label_names=['x','y','z'], show_ticks=True, **kwargs):
    """
    Generate a complete frame for a 3D graphics object.
    This is a workaround for the lack of complete frames in 
    Sage 3D plots. It creates a background frame behind the
    plot, set ticks, gridlines and labels as text3d objects
    at locations determined from the bounding box of the 
    graphic object ``figure``.

    INPUT:

    - ``figure`` -- a 3D graphic object, as an instance of
        :class:`~sage.plot.plot3d.base.Graphics3d`
    - ``grid`` -- list with the number of gridlines and ticks
        in the x, y and z direction respectively
    - ``colors`` -- list with the background frame color and
        gridline color respectively
    - ``alpha`` -- transparency of the background frame
    - ``resize_factor`` -- string for the z-axis label
    - ``cube_ratio`` -- string for the z-axis label
    - ``show_labels`` -- Boolean. Show or not the labels
    - ``label_names`` -- ist of strings with the x-axis label,
        the y-axis label and the z-axis label.
    - ``show_ticks`` -- Boolean. Show or not the tickmarks
    - ``**kwds`` -- options (e.g. aspect_ratio) for the
        3D output object

    OUTPUT:

    - the 3D graphic object with text3d labels added.

    EXAMPLE::

         sage: g = sphere()
         sage: print g
         Graphics3d Object
         sage: show(g)  # no complete frame
         sage: ga = set_3dframe(g)
         sage: print ga
         Graphics3d Object
         sage: show(ga)  # the 3D frame has now background, 
         axes labels and tickmarks.
    """
    frame = set_background_frame(lower_left,upper_right, color=frame_color, frame=False, **kwargs)
    frame += set_frame_gridlines(lower_left,upper_right, grid=grid, color=gridline_color)
    if show_labels and not show_axes:
        frame += set_axes_labels(lower_left, upper_right, label_names, 
                              fontfamily='serif', fontweight='bold', fontsize='140%')
    if show_ticks:
        frame += set_frame_ticks(lower_left,upper_right,grid=grid, 
                              fontfamily='serif')
    if show_axes:
        frame += set_axes(lower_left, upper_right, label_names, fontfamily='serif', fontweight='bold', fontsize='140%')
    return frame



def set_axes(lower_left, upper_right, label_names, **kwargs):
    from sage.modules.free_module_element import vector
    from sage.plot.plot3d.shapes2 import text3d
    x_length,y_length,z_length = [(ur - ll)*6/5 for ll,ur in zip(lower_left,upper_right)]
    v0 = vector(lower_left)
    vx = vector([x_length,0,0])
    vy = vector([0,y_length,0])
    vz = vector([0,0,z_length])
    size = max(x_length,y_length,z_length)
    vectors = sum((v.plot(color='gray',frame=False,thickness=size*4/6, start=v0) for v in (vx,vy,vz)))
    labels = sum([text3d(l,1.1*v+v0,**kwargs) for l,v in zip(label_names,(vx,vy,vz))])
    return vectors+labels


def grid_slices(lower_left, upper_right, grid):
    """
    Helper function generating a list of gridline positions for a 3-D frame.
    
    Primarily used as a helper function for creating frames for 3-D
    graphics viewing.

    INPUT:

    - ``lower_left`` -- list, tuple, or vector; the lower left corner
    of the frame.

    - ``upper_right`` -- list, tuple, or vector; the upper right corner
    of the frame.
      
    - ``grid`` -- list, tuple or vector; the number of gridlines 
      in the x, y and z direction respectivelly.


    EXAMPLES:

    We can use it directly::

        sage: grid_slices([1,2,3],[4,5,6], grid=(4,4,4))
        <generator object grid_slices.<locals>.<genexpr> at 0x7fac306d4f90>

        sage: background_frame([1,2,3],[3,7,9], grid=(3,5,6))
        <generator object grid_slices.<locals>.<genexpr> at 0x7fac306d4f90>
    """
    from sage.arith.srange import srange
    steps = ((b-a)/(c-1) for a,b,c in zip(lower_left, upper_right, grid))
    return (srange(a+c,b,c, include_endpoint=True) for a,b,c in zip(lower_left, upper_right, steps))
	


def set_background_frame(lower_left, upper_right, **kwargs):
    """
    Draw a background of polygons for in 3D graphics.

    Primarily used as a helper function for creating frames for 3-D
    graphics viewing.

    INPUT:

    - ``lower_left`` -- list, tuple, or vector; the lower left corner
    of the frame.

    - ``upper_right`` -- list, tuple, or vector; the upper right corner
    of the frame.


    EXAMPLES:

    We can use it directly::

        sage: background_frame([1,2,3],[4,5,6])
        Graphics3d Object

        sage: background_frame([1,2,3],[3,7,9], color='gray)
        Graphics3d Object
    """
    from sage.plot.plot3d.shapes2 import polygon3d
    if 'theme' in kwargs.keys() and kwargs['theme'] == 'dark' and 'color' in kwargs.keys() and kwargs['color'] == 'white':
        kwargs['color']='black'
        kwargs['alpha']=.1
    xmin, ymin, zmin = lower_left
    xmax, ymax, zmax = upper_right
    xz_plane = polygon3d([lower_left, (xmin, ymin, zmax), (xmax, ymin, zmax),
                          (xmax, ymin, zmin), lower_left], **kwargs)
    xy_plane = polygon3d([lower_left, (xmin, ymax, zmin), (xmax, ymax, zmin),
                          (xmax, ymin, zmin), lower_left], **kwargs)
    yz_plane = polygon3d([lower_left, (xmin, ymax, zmin), (xmin, ymax, zmax),
                          (xmin, ymin, zmax), lower_left], **kwargs)
    planes = xz_plane + xy_plane + yz_plane
    return planes
    
    
def set_frame_gridlines(lower_left, upper_right, grid, **kwargs):
    """
    Draw correct gridlines for a given frame in 3-D.

    Primarily used as a helper function for creating frames for 3-D
    graphics viewing.

    INPUT:
    
    - ``lower_left`` -- list, tuple, or vector; the lower left corner
    of the frame.

    - ``upper_right`` -- list, tuple, or vector; the upper right corner
    of the frame.

    - ``grid`` -- list, tuple or vector; the number of gridlines 
      in the x, y and z direction respectivelly.

    EXAMPLES:

    We can use it directly::

        sage: frame_gridlines([1,2,3],[4,5,6], grid=(4,4,4))
        Graphics3d Object

        sage: frame_gridlines([1,2,3],[3,7,9], grid=(3,5,6))
        Graphics3d Object
    """
    from sage.plot.plot3d.shapes2 import line3d
    xmin, ymin, zmin = lower_left
    xmax, ymax, zmax = upper_right
    xcoords, ycoords, zcoords = grid_slices(lower_left, upper_right, grid)
    x_gridlines = sum([line3d([(xc, ymax, zmin), (xc, ymin, zmin),
                      (xc, ymin, zmax)], **kwargs) for xc in xcoords])
    y_gridlines = sum([line3d([(xmax, yc, zmin), (xmin, yc, zmin),
                      (xmin, yc, zmax)], **kwargs) for yc in ycoords])
    z_gridlines = sum([line3d([(xmax, ymin, zc), (xmin, ymin, zc),
                      (xmin, ymax, zc)], **kwargs) for zc in zcoords])
    border = line3d([(xmin, ymin, zmax), (xmax, ymin, zmax),(xmax, ymin, zmin),(xmax, ymax, zmin), 
                    (xmin, ymax, zmin), (xmin, ymax, zmax), (xmin, ymin, zmax)], thickness=2, **kwargs)
    return x_gridlines + y_gridlines + z_gridlines + border
    

def set_axes_labels(lower_left, upper_right, label_names, **kwds):
    r"""
    Set axes labels for a 3D graphics object.
    Primarily used as a helper function for creating frames for 3-D
    graphics viewing. 

    INPUT:

    - ``lower_left`` -- list, tuple, or vector; the lower left corner
    of the frame.

    - ``upper_right`` -- list, tuple, or vector; the upper right corner
    of the frame.
      
    - ``label_names`` -- list of strings with the x-axis label,
      the y-axis label and the z-axis label.
      
    - ``**kwds`` -- options (e.g. color) for text3d

    OUTPUT:

    - A 3D graphic object with text3d labels.

    EXAMPLE::

         sage: g = sphere()
         sage: print g
         Graphics3d Object
         sage: show(g)  # no axes labels
         sage: ga = g + axes_labels((0,0,0), (2,2,2), ['X', 'Y', 'Z'], color='red')
         sage: print ga
         Graphics3d Object
         sage: show(ga)  # the 3D frame has now axes labels
    """
    from sage.plot.plot3d.shapes2 import text3d
    xmin, ymin, zmin = lower_left
    xmed, ymed, zmed = (a + (b - a)/2 for a, b in zip(lower_left,upper_right))
    x1, y1, z1 = (b + (b - a)/5 for a, b in zip(lower_left,upper_right))
    xlabel, ylabel, zlabel = label_names
    labels = text3d(xlabel, (xmed, y1, zmin), **kwds)
    labels += text3d(ylabel, (x1, ymed, zmin), **kwds)
    labels += text3d(zlabel, (x1, ymin, zmed), **kwds)
    return labels

    
def set_frame_ticks(lower_left, upper_right, grid, eps=1, **kwargs):
    r"""
    Draw tickmarks for 3D frames.

    Primarily used as a helper function for creating frames for 3-D
    graphics viewing.

    INPUT:

    - ``lower_left`` -- list, tuple, or vector; the lower left corner
    of the frame.

    - ``upper_right`` -- list, tuple, or vector; the upper right corner
    of the frame.

    - ``eps`` -- (default: 1) a parameter for how far away from the frame
      to put the labels.

    EXAMPLES:

    We can use it directly::

        sage: frame_ticks([1,2,3],[4,5,6])
        Graphics3d Object

        sage: frame_ticks([1,2,3],[3,7,9], grid=(3,5,6))
        Graphics3d Object
    """
    from sage.plot.plot3d.shapes2 import text3d
    xmin, ymin, zmin = lower_left
    xmax, ymax, zmax = upper_right
    xcoords, ycoords, zcoords = grid_slices(lower_left, upper_right, grid)
    if eps == 1: eps = 1.2*eps
    x_ticks = sum([text3d(round(xc, 2),(xc, eps*ymax, zmin), 
                           **kwargs) for xc in xcoords])
    y_ticks = sum([text3d(round(yc, 2),(eps*xmax, yc, zmin), 
                           **kwargs) for yc in ycoords])
    z_ticks = sum([text3d(round(zc, 2),(eps*xmax, ymin, zc),
                           **kwargs) for zc in zcoords])
    return x_ticks + y_ticks + z_ticks

var('x y')

f3d(plot3d((x^2 + y^2),(x,-3,3),(y,-3,3), plot_points=200))

Graphics3d Object